## Alinging Raster DEM to sparse altimetry points [Preliminary/in-progress, please be patient]
#### Adapted from the [ASP Documentation](https://stereopipeline.readthedocs.io/en/latest/tools/pc_align.html#pc-align)

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import requests
import numpy as np
import os,sys,glob
import matplotlib.pyplot as plt
import geopandas as gpd
from mpl_toolkits.axes_grid1 import make_axes_locatable
from distutils.spawn import find_executable
import dask
import zipfile
from pyproj import Proj, transform
import subprocess
from fetch_dem import opentopo_utils
import asp_binder_utils as asp_utils
import xyzservices
import rioxarray
import rasterio
from shapely.geometry import box
from sliderule import sliderule, icesat2

import xyzservices

## Universal settings

In [22]:
terrain_map = xyzservices.providers.Esri.WorldImagery() #Used to render basemap
#verbose = False #  Will only print the bash commands and whether the process ran sucessfully or not
verbose = True # will print all the logs printed by ASP
alignment_algortihm = 'point-to-point' # suggested to use point-to-point if the terrain variability is low (more flat terrain cases)
max_displacement = 30 #you might have to play with this to adapt to different datasets
tsrs = 'EPSG:32610' # input projection
tr = 30 #DEM resolution

## Preprocessing 0: Data Download
* For the purpose of this tutorial, we will register the ASTER DEM produced using the stereo processing tutorial to sparse elevation values derived by the [ICESat-2 altimetry mission](https://icesat-2.gsfc.nasa.gov/).
    * To run this tutorial without running the stereo processing tutorial, we have archived the ASTER DEM produced using the ASTER camera models and orthorectified imagery (Type 3) on [Zenodo](https://zenodo.org/records/10208419). We will fetch it directly from zenodo.
    * We will download ICESat-2 using the [Sliderule Earth](https://slideruleearth.io/web/) package.



* Alternatively, users can bring their own source DEM, and explore the tutorial using the same! Please follow the below guidelines to do so.
    * To perform this in a github codespace session, go to the file explorer on the right, do a right click and select upload, then upload the DEMs of your choice from the file browser.
    * See also this [stack exhange answer](https://stackoverflow.com/questions/62284623/how-can-i-upload-a-file-to-a-github-codespaces-environment)

* When you change the DEMs to a different site than the site used by default, make sure to change the projected corrdinate system definition (t_srs) 

### 0.1 Download ASTER ASP DEM over Mt. Rainier

In [4]:
aster_dem_fn = 'aster_orthorectified-DEM.tif'
#ASTER Sample has been staged on Zenodo:
#https://zenodo.org/record/7972223/files/AST_L1A_00307312017190728_20200218153629_19952.zip?download=1
zenodo_url = 'https://zenodo.org/records/10208419/files/aster_orthorectified-DEM.tif?download=1'
if os.path.exists(aster_dem_fn):
    print(f"file {aster_dem_fn} already downloaded")
else:
    response = requests.get(zenodo_url)
    #Check for 200
    if response.ok:
        print ('OK!')
    else:
        print ('Query failed')
        sys.exit()
    #Write to disk
    open(aster_dem_fn, 'wb').write(response.content)
    print(f"file {aster_dem_fn} saved")

file aster_orthorectified-DEM.tif already downloaded


### 0.2 Query ICESat-2 points over DEM extent and limit to during snow-free conditions

In [5]:

# get aoi extent in geographic coordinates
geo_crs = 'EPSG:4326'
aoi_extent = asp_utils.subsetBBox(aster_dem_fn,geo_crs)
aoi_box = gpd.GeoDataFrame({'idx':[0],'geometry':box(*aoi_extent)},crs=geo_crs)
#in_crs = rasterio.open(dem_file).crs

/srv/conda/envs/notebook/lib/python3.9/site-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/srv/conda/envs/notebook/lib/python3.9/site-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/workspaces/asp_tutorials/tutorials/asp_binder_utils.py:114: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
 

In [6]:
region = sliderule.toregion(aoi_box)
# Build ATL06 Request Parameters
parms = {
    "poly": region["poly"],
    "srt": icesat2.SRT_LAND,
    "cnf": icesat2.CNF_SURFACE_HIGH,
    "ats": 7.0,
    "cnt": 10,
    "len": 40.0,
    "res": 20.0,
    
}

# Make ATL06 Request
atl06 = icesat2.atl06p(parms) #dataframe with ICESat-2 points over the study area

In [7]:
## Plot ICESat-2 points over the aoi
atl06.reset_index()[['geometry','h_mean']].sample(n=10000).explore(column='h_mean',style_kwds=dict(fill=False),tiles=terrain_map)

In [8]:
atl06.crs

<Geographic 3D CRS: EPSG:7912>
Name: ITRF2014
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
- h[up]: Ellipsoidal height (metre)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: International Terrestrial Reference Frame 2014
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

In [12]:
wgs84_projection = 'EPSG:4326'+'EPSG:4979'
atl06_epsg_4326 = atl06.to_crs(epsg="4326+4979")

In [13]:
atl06_epsg_4326.crs

<Geographic 3D CRS: EPSG:4979>
Name: WGS 84
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
- h[up]: Ellipsoidal height (metre)
Area of Use:
- name: World.
- bounds: (-180.0, -90.0, 180.0, 90.0)
Datum: World Geodetic System 1984 ensemble
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

### 0.3 Save ICESat-2 points to disk for alignment purposes 

In [14]:
atl06_epsg_4326['lon'] = atl06_epsg_4326.geometry.x
atl06_epsg_4326['lat'] = atl06_epsg_4326.geometry.y
altimetry_csv_fn_all = 'ICESat-2_all_control_points.csv'
atl06_epsg_4326[['lon','lat','h_mean']].to_csv(altimetry_csv_fn_all,index=False)

## 1. Perform Co-registration (using ASP's [pc_align](https://stereopipeline.readthedocs.io/en/latest/tools/pc_align.html) algorithm)

In [23]:

pc_align = find_executable('pc_align')
ref_alitmetry = altimetry_csv_fn_all
src_dem = aster_dem_fn
alignment_dir  = 'alignment_sparse_altimetry_all/aster_aligned2ICESat2'
#csv_proj4 = '+proj=longlat +ellps=GRS80 +no_defs +type=crs' #EPSG:7912 (https://epsg.io/7912#google_vignette)
csv_proj4 = '+proj=longlat +datum=WGS84 +no_defs +type=crs' #EPSG:4326 https://epsg.io/4326#google_vignette
altimetry_datum = 'WGS84'
csv_format = '1:lon,2:lat,3:height_above_datum'
alignment_call = f"{pc_align}  --compute-translation-only --highest-accuracy  --csv-format '{csv_format}' --csv-proj4 '{csv_proj4}' --save-transformed-source-points --alignment-method {alignment_algortihm}  --max-displacement {max_displacement} {ref_alitmetry} {src_dem} -o {alignment_dir}"
asp_utils.run_bash_command(alignment_call,verbose=verbose)

/srv/StereoPipeline/bin/pc_align  --compute-translation-only --highest-accuracy  --csv-format '1:lon,2:lat,3:height_above_datum' --csv-proj4 '+proj=longlat +datum=WGS84 +no_defs +type=crs' --save-transformed-source-points --alignment-method point-to-point  --max-displacement 30 ICESat-2_all_control_points.csv aster_orthorectified-DEM.tif -o alignment_sparse_altimetry_all/aster_aligned2ICESat2
	--> Setting number of processing threads to: 4
Writing log info to: alignment_sparse_altimetry_all/aster_aligned2ICESat2-log-pc_align-02-28-0045-35009.txt
Will use datum (for CSV files): Geodetic Datum --> Name: WGS_1984  Spheroid: WGS 84  Semi-major axis: 6378137  Semi-minor axis: 6356752.3142451793  Meridian: Greenwich at 0  Proj4 Str: +datum=WGS84
Computing the intersection of the bounding boxes of the reference and source points using 9000000 sample points.
Reference box: (Origin: (-122.344, 46.7219) width: 0.98973 height: 0.60749)
Source box:    (Origin: (-122.343, 46.7159) width: 0.981249 h

writing to alignment_sparse_altimetry_all/aster_aligned2ICESat2-iterationInfo.csv


Match ratio: 0.75001
Alignment took 2.77872 [s]
Number of errors: 100000
Output: error percentile of smallest errors (meters): 16%: 10.525, 50%: 18.5082, 84%: 26.4191
Output: mean of smallest errors (meters): 25%: 9.12095, 50%: 12.4115, 75%: 15.3627, 100%: 18.5653
Final error computation took 0.027276 [s]
Alignment transform (origin is planet center):
                 1                  0                  0 -3.904767240397632
                 0                  1                  0 -10.77550417324528
                 0                  0                  1  -4.60501157399267
                 0                  0                  0                  1
Centroid of source points (Cartesian, meters): Vector3(-2303546.8,-3696520.7,4644753.5)
Centroid of source points (lat,lon,z): Vector3(47.032563,-121.92977,711.48097)

Translation vector (Cartesian, meters): Vector3(-3.9047672,-10.775504,-4.6050116)
Translation vector (North-East-Down, meters): Vector3(-11.341726,2.384977,-4.2710614)
Transl

Child returned 0


In [ ]:
## Initial Differenc

In [23]:
# Limit points to snow-free month (in case of Mt. Rainier, September)
snow_free_month = 9
mask = atl06.index.month == snow_free_month
atl06_snow_free = atl06[mask]

In [34]:
atl06_snow_free.shape
print(f"From total {len(atl06)} ICESat-2 points, {len(atl06_snow_free)} points were acquired in September")

From total 630483 ICESat-2 points, 45649 points were acquired in September


In [32]:
atl06_snow_free.reset_index()[['geometry','h_mean']].sample(n=10000).explore(column='h_mean',style_kwds=dict(fill=False),tiles=terrain_map)

In [39]:
atl06_snow_free['lon'] = atl06_snow_free.geometry.x
atl06_snow_free['lat'] = atl06_snow_free.geometry.y
altimetry_csv_fn = 'ICESat-2_september_control_points.csv'
atl06_snow_free[['lon','lat','h_mean']].to_csv(altimetry_csv_fn,index=False)

/srv/conda/envs/notebook/lib/python3.8/site-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/srv/conda/envs/notebook/lib/python3.8/site-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


/srv/StereoPipeline/bin/pc_align --compute-translation-only --highest-accuracy  --csv-format '1:lon 2:lat 3:height_above_datum' --csv-proj4 '+proj=longlat +ellps=GRS80 +no_defs +type=crs' --save-transformed-source-points --alignment-method point-to-plane  --max-displacement 40 ICESat-2_september_control_points.csv aster_orthorectified-DEM.tif -o alignment_sparse_altimetry/aster_aligned2ICESat2
	--> Setting number of processing threads to: 4
Writing log info to: alignment_sparse_altimetry/aster_aligned2ICESat2-log-pc_align-12-01-0431-32490.txt
Will use datum (for CSV files): Geodetic Datum --> Name: Unknown based on GRS80 ellipsoid  Spheroid: GRS 1980  Semi-major axis: 6378137  Semi-minor axis: 6356752.3141403561  Meridian: Greenwich at 0  Proj4 Str: +ellps=GRS80
Computing the bounding boxes of the reference and source points using 9000000 sample points.
Computation of bounding boxes took 2.81773 [s]
Reference points box: (Origin: (-122.344, 46.722) width: 0.933134 height: 0.607444)
Sou

writing to alignment_sparse_altimetry/aster_aligned2ICESat2-iterationInfo.csv


Match ratio: 0.750005
Alignment took 0.247312 [s]
Number of errors: 51717
Output: error percentile of smallest errors (meters): 16%: 13.1917, 50%: 23.7284, 84%: 38.3264
Output: mean of smallest errors (meters): 25%: 11.4359, 50%: 15.6948, 75%: 19.7846, 100%: 25.1424
Final error computation took 0.009907 [s]
Alignment transform (origin is planet center):
                 1                  0                  0 -4.005573328118771
                 0                  1                  0 -23.70012195501477
                 0                  0                  1 -11.54963019676507
                 0                  0                  0                  1
Centroid of source points (Cartesian, meters): Vector3(-2293198.4,-3706600.3,4642343.6)
Centroid of source points (lat,lon,z): Vector3(46.99736,-121.74424,1065.1476)

Translation vector (Cartesian, meters): Vector3(-4.0055733,-23.700122,-11.54963)
Translation vector (North-East-Down, meters): Vector3(-24.158025,9.0629471,-6.736999)
Transl

Child returned 0


## Shashank TODO:
* Figure out altimetry_datum conversion
* Run using all points probably
* Plot results

NameError: name 'csv_format' is not defined